In [1]:
import pandas as pd
import time
import random
import math
import mmh3
from statistics import mean

# DBLP

## Teste de tempo de permancia dos blocos: usando descarte

In [2]:
def str_to_MinHash(str1, q, seed=0):
    return min([mmh3.hash(str1[i:i + q], seed) for i in range(len(str1) - q + 1)])

def frequent2(temp, L, t):
    return {k: v for (k, v) in temp.items() if v/L >= t}

def matching():
    global tp, fp, pairsNo, L1, q
    for index2 in range(nbS, nbS + offsetB): 
        if index2 > len(df2) - 1:
            return True

        rr = df2.iloc[index2, 0:5]
        idScholar = rr["id"]
        title = rr["title"]
        authors = rr["authors"]
        srec = title + " " + authors

        temp = dict()
        indices = [random.randrange(0, L) for i in range(L1)]
        matchingPairs = {}
        for l in indices:
            key = str(str_to_MinHash(srec.lower(), q, l))
            d = dictB[l]
            if key in d:
                ids = d[key]
                for id in ids:
                    if id in temp:
                        temp[id] += 1
                        if temp[id] / L1 >= t:
                            matchingPairs[id] = 1
                    else:
                        temp[id] = 1
        for id in matchingPairs.keys():
            idDBLP = id
            pairsNo += 1
            if idDBLP in truthD:
                ids = truthD[idDBLP]
                for id in ids:
                    if id == idScholar:
                        tp += 1
                        break
            else:
                fp += 1

    return False

def elimina_elementos_dentro_dictB(array_para_descarte, array_para_descarte_igual, elementos_para_descarte):
    indice = 0
    for (tempo_inserido) in array_para_descarte_igual:
        if tempo_inserido < elementos_para_descarte:
            indice += 1
        else:
            del array_para_descarte[:indice]
            del array_para_descarte_igual[:indice]
            break

def normaliza_para_0(array,elementoAtualParaDescarte):
    return [e - elementoAtualParaDescarte for e in array]

In [3]:
df1 = pd.read_csv("../00-datasets/DBLP.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/Scholar.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/truth.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    idDBLP = r["idDBLP"]
    idScholar = r["idScholar"]
    if idDBLP in truthD:
        ids = truthD[idDBLP]
        ids.append(idScholar)
    else:
        truthD[idDBLP] = [idScholar]

t = 0.5
TP = 5347
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0

L= 116 L1= 50


In [ ]:
tempoQueFoiInseridoNaEstrutura = 0 # esse é o valor que sera colocado junto com o id, seria a posiçaõ do elemento no array
elementos_para_descarte = 50 # esse é a quantidade de elementos que serão descartados
acompanhamentoIndicePorBloco = {} #essa estrutura é um indice que vai ser usada para saber qual a posição do elemento que será descartado

tempo_permanencia = []
while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:5]
        idDBLP = rr["id"]
        title = rr["title"]
        authors = rr["authors"]

        srec = title + " " + authors
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                if len(ids) < w:
                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]
                    
                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - 50)
                    # print(elementoAtualParaDescarte)
                    # print(ids_igual)
                    # print(array_normalizado)
                    # print("\n\n\n")
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)

                    elimina_elementos_dentro_dictB(ids, ids_igual, elementoAtualParaDescarte)
                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + 50]

                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
            else:
                d[key] = [idDBLP]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, 50]

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()

    blockingTime += (end - st)
    st = time.time()
    termination = matching()  
    end = time.time()
    matchingTime += (end - st)
    # if termination:
    #         break
    if naS >= len(df1):
        break
    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

50
[0, 1, 2, 5, 6, 8, 10, 11, 12, 14, 15, 16, 17, 18, 19, 21, 22, 23, 24, 27, 28, 29, 30, 32, 34, 37, 38, 41, 42, 43, 46, 47, 54, 55, 56, 57, 58, 60, 61, 63, 64, 65, 66, 71, 72, 73, 79, 81, 84, 85, 86, 87, 90, 92, 94, 98, 102, 103, 104, 105, 106, 108, 109, 110, 112, 113, 114, 117, 118, 119, 125, 127, 130, 131, 132, 133, 136, 137, 138, 139, 140, 142, 144, 145, 148, 151, 152, 154, 155, 156, 157, 158, 159, 161, 162, 163, 164, 166, 167, 170, 172, 173, 175, 176, 177, 178, 180, 182, 183, 186, 189, 190, 191, 192, 193, 195, 196, 197, 198, 199, 204, 206, 207, 209, 210, 211, 212, 215, 218, 219, 220, 222, 224, 226, 227, 229, 230, 231, 232, 233, 234, 235, 236, 238, 240, 245, 248, 250, 251, 253, 255, 257, 258, 259, 261, 262, 263, 264, 265, 266, 268, 269, 270, 273, 274, 275, 278, 280, 283, 284, 285, 286, 287, 288, 289, 291, 292, 293, 294, 296, 297, 298, 300, 302, 303, 305, 306, 307, 312, 313, 315, 320, 321, 324, 327, 328, 329, 330, 331, 333, 334, 335, 336, 337, 338, 339, 340, 347, 349, 351, 352, 353

In [5]:
mean(tempo_permanencia)
#979.4007080291971

979.4007080291971

## Teste de tempo de permancia dos blocos: usando pop

In [ ]:
df1 = pd.read_csv("../00-datasets/DBLP.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/Scholar.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/truth.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    idDBLP = r["idDBLP"]
    idScholar = r["idScholar"]
    if idDBLP in truthD:
        ids = truthD[idDBLP]
        ids.append(idScholar)
    else:
        truthD[idDBLP] = [idScholar]

t = 0.5
TP = 5347
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0

In [ ]:
tempoQueFoiInseridoNaEstrutura = 0  # Contador de inserção
elementos_para_descarte = 1  # Quantidade de elementos descartados
acompanhamentoIndicePorBloco = {}  # Índice para rastrear descartes

tempo_permanencia = []  # Lista para armazenar os tempos de permanência

while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:5]
        idDBLP = rr["id"]
        title = rr["title"]
        authors = rr["authors"]

        srec = title + " " + authors
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                if len(ids) < w:
                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]
                    print(key)
                    print(elementoAtualParaDescarte - elementos_para_descarte)
                    print(ids_igual)                   
                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - elementos_para_descarte)
                    print(array_normalizado)
                    print("\n\n\n")
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)
            
                    ids.pop(0)
                    ids_igual.pop(0)
                    # elimina_elementos_dentro_dictB(ids, ids_igual, elementoAtualParaDescarte)
                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + elementos_para_descarte]

                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)

            else:
                # Cria uma nova entrada no dicionário
                d[key] = [idDBLP]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, elementos_para_descarte]

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()

    blockingTime += (end - st)
    st = time.time()
    # termination = matching()  
    end = time.time()
    matchingTime += (end - st)
    # if termination:
    #     break
    
    if naS >= len(df1):
        break

    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

In [ ]:
mean(tempo_permanencia)
#1132.0064994299928

## Teste de tempo de permanencia usando tamanho de blocos variados

In [ ]:
def exclui_blocos(dictB, dictB_igual, tempoQueFoiInseridoNaEstrutura,tamanhoDosBlocos):
    for l, blocos_da_pos in enumerate(dictB_igual):
        for key, bloco_unico in blocos_da_pos.items():
            if bloco_unico[-1] < tempoQueFoiInseridoNaEstrutura - 300 and tamanhoDosBlocos[(key, l)] > 100:
                tamanhoDosBlocos[(key, l)] -= 100
            break

In [25]:
df1 = pd.read_csv("../00-datasets/DBLP.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/Scholar.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/truth.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    idDBLP = r["idDBLP"]
    idScholar = r["idScholar"]
    if idDBLP in truthD:
        ids = truthD[idDBLP]
        ids.append(idScholar)
    else:
        truthD[idDBLP] = [idScholar]

t = 0.5
TP = 5347
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0

L= 116 L1= 50


In [26]:
tempoQueFoiInseridoNaEstrutura = 0 # esse é o valor que sera colocado junto com o id, seria a posiçaõ do elemento no array
elementos_para_descarte = 50 # esse é a quantidade de elementos que serão descartados
acompanhamentoIndicePorBloco = {} #essa estrutura é um indice que vai ser usada para saber qual a posição do elemento que será descartado
tamanhoDosBlocos = {}

tempo_permanencia = []
while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:5]
        idDBLP = rr["id"]
        title = rr["title"]
        authors = rr["authors"]

        srec = title + " " + authors
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                tamanho_atual = tamanhoDosBlocos[(key, l)]
                if len(ids) < tamanho_atual:
                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]

                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - 50)
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)

                    # print(elementoAtualParaDescarte)
                    # print(ids_igual)
                    # print(array_normalizado)
                    # print("\n\n\n")   
                    elimina_elementos_dentro_dictB(ids, ids_igual, elementoAtualParaDescarte)
                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + elementos_para_descarte]
                    
                    ids.append(idDBLP)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                    
                    exclui_blocos(dictB, dictB_igual, tempoQueFoiInseridoNaEstrutura, tamanhoDosBlocos)
                    tamanhoDosBlocos[(key, l)] += 100
            else:
                d[key] = [idDBLP]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, elementos_para_descarte]
                tamanhoDosBlocos[(key, l)] = w

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()

    blockingTime += (end - st)
    st = time.time()
    termination = matching()  
    end = time.time()
    matchingTime += (end - st)
    if termination:
            break
    # if naS >= len(df1):
    #     break
    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

blocking time (in mins) 0.1020458459854126
matching time (in mins) 4.592520737648011
TP= 5048 Recall= 0.9440807929680195 Precision= 0.6433031731872053 pairsNo= 91656


In [28]:
mean(tempo_permanencia)

1112.9509245930187

# NCVR

In [3]:
def str_to_MinHash(str1, q, seed=0):
    return min([mmh3.hash(str1[i:i + q], seed) for i in range(len(str1) - q + 1)])

def frequent2(temp, L, t):
    return {k: v for (k, v) in temp.items() if v/L >= t}

def matching():
    global tp, fp, pairsNo, L1, q
    for index2 in range(nbS, nbS + offsetB):  # DBLP
        if index2 > len(df2) - 1:
            return True

        rr = df2.iloc[index1]
        ncid = rr["id"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)

        temp = dict()
        indices = [random.randrange(0, L) for i in range(L1)]
        matchingPairs = {}
        for l in indices:
            key = str(str_to_MinHash(srec.lower(), q, l))
            d = dictB[l]
            if key in d:
                ids = d[key]
                for id in ids:
                    if id in temp:
                        temp[id] += 1
                        if temp[id] / L1 >= t:
                            matchingPairs[id] = 1
                    else:
                        temp[id] = 1
        for id in matchingPairs.keys():
            idDBLP = id
            pairsNo += 1
            if idDBLP in truthD:
                ids = truthD[idDBLP]
                for id in ids:
                    if id == ncid:
                        tp += 1
                        break
            else:
                fp += 1

    return False

def normaliza_para_0(array,elementoAtualParaDescarte):
    return [e - elementoAtualParaDescarte for e in array]

In [ ]:
df1 = pd.read_csv("../00-datasets/ncvoter42.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/perturbed_recordsNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/ground_truthNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    novoId = r["novoId"]
    antigoId = r["antigoId"]
    if antigoId in truthD:
        ids = truthD[antigoId]
        ids.append(novoId)
    else:
        truthD[antigoId] = [novoId]

t = 0.5
p1 = (t) ** 8
L = math.ceil(math.log(0.1) / math.log(1 - p1))
# print("Minhash LSH=", L)
TP = 40893
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0

L= 116 L1= 50


In [ ]:
#Aqui com o offset a 50
tempoQueFoiInseridoNaEstrutura = 0
tempo_permanencia = []
acompanhamentoIndicePorBloco = {}
elementos_para_descarte = 1

while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):  # Scholar
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:69]

        ncid = rr["ncid"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                if len(ids) < w:
                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]
                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - elementos_para_descarte)
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)
                    # print(key)
                    # print(elementoAtualParaDescarte - elementos_para_descarte)
                    # print(ids_igual)                   
                    # print(array_normalizado)
                    # print("\n\n\n")
                    

                    ids.pop(0)
                    ids_igual.pop(0)

                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + elementos_para_descarte]

                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
            else:
                d[key] = [ncid]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, elementos_para_descarte]

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()
    blockingTime += (end - st)
    st = time.time()
    termination = matching() 
    end = time.time()
    matchingTime += (end - st)
    if termination:
            break

    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

blocking time (in mins) 11.911125938097635
matching time (in mins) 3.25330673456192
TP= 34941 Recall= 0.8544494167705964 Precision= 0.3058855457020546 pairsNo= 191062


In [15]:
mean(tempo_permanencia)

17146.77038685162

In [25]:
import pandas as pd
import time
import random
import math
import mmh3

def str_to_MinHash(str1, q, seed=0):
    return min([mmh3.hash(str1[i:i + q], seed) for i in range(len(str1) - q + 1)])

def frequent2(temp, L, t):
    return {k: v for (k, v) in temp.items() if v/L >= t}

def matching():
    global tp, fp, pairsNo, L1, q
    for index2 in range(nbS, nbS + offsetB): 
        if index2 > len(df2) - 1:
            return True

        rr = df2.iloc[index1]
        ncid = rr["id"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)

        temp = dict()
        indices = [random.randrange(0, L) for i in range(L1)]
        matchingPairs = {}
        for l in indices:
            key = str(str_to_MinHash(srec.lower(), q, l))
            d = dictB[l]
            if key in d:
                ids = d[key]
                for id in ids:
                    if id in temp:
                        temp[id] += 1
                        if temp[id] / L1 >= t:
                            matchingPairs[id] = 1
                    else:
                        temp[id] = 1
        for id in matchingPairs.keys():
            idDBLP = id
            pairsNo += 1
            if idDBLP in truthD:
                ids = truthD[idDBLP]
                for id in ids:
                    if id == ncid:
                        tp += 1
                        break
            else:
                fp += 1

    return False


def elimina_elementos_dentro_dictB(array_para_descarte, array_para_descarte_igual, elementos_para_descarte):
    indice = 0
    for (tempo_inserido) in array_para_descarte_igual:
        if tempo_inserido < elementos_para_descarte:
            indice += 1
        else:
            del array_para_descarte[:indice]
            del array_para_descarte_igual[:indice]
            break



In [26]:
df1 = pd.read_csv("../00-datasets/ncvoter42.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/perturbed_recordsNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/ground_truthNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    novoId = r["novoId"]
    antigoId = r["antigoId"]
    if antigoId in truthD:
        ids = truthD[antigoId]
        ids.append(novoId)
    else:
        truthD[antigoId] = [novoId]

t = 0.5
TP = 40893
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0


tempoQueFoiInseridoNaEstrutura = 0 # esse é o valor que sera colocado junto com o id, seria a posiçaõ do elemento no array
elementos_para_descarte = 50 # esse é a quantidade de elementos que serão descartados
acompanhamentoIndicePorBloco = {} #essa estrutura é um indice que vai ser usada para saber qual a posição do elemento que será descartado
tempo_permanencia = []


L= 116 L1= 50


In [28]:
while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:69]
        
        ncid = rr["ncid"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                if len(ids) < w:
                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]
                    elimina_elementos_dentro_dictB(ids, ids_igual, elementoAtualParaDescarte)
                    
                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - elementos_para_descarte)
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)

                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + elementos_para_descarte]
                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)


            else:
                d[key] = [ncid]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, elementos_para_descarte]

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()

    blockingTime += (end - st)
    st = time.time()
    termination = matching()  
    end = time.time()
    matchingTime += (end - st)
    if termination:
            break

    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

blocking time (in mins) 3.2078996221224467
matching time (in mins) 3.523145536581675
TP= 34941 Recall= 0.8544494167705964 Precision= 0.3067825628868695 pairsNo= 190061


In [30]:
mean(tempo_permanencia)

8020.2521824487585

In [32]:
import pandas as pd
import time
import random
import math
import mmh3

def str_to_MinHash(str1, q, seed=0):
    return min([mmh3.hash(str1[i:i + q], seed) for i in range(len(str1) - q + 1)])

def frequent2(temp, L, t):
    return {k: v for (k, v) in temp.items() if v/L >= t}

def matching():
    global tp, fp, pairsNo, L1, q
    for index2 in range(nbS, nbS + offsetB): 
        if index2 > len(df2) - 1:
            return True

        rr = df2.iloc[index1]
        ncid = rr["id"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)

        temp = dict()
        indices = [random.randrange(0, L) for i in range(L1)]
        matchingPairs = {}
        for l in indices:
            key = str(str_to_MinHash(srec.lower(), q, l))
            d = dictB[l]
            if key in d:
                ids = d[key]
                for id in ids:
                    if id in temp:
                        temp[id] += 1
                        if temp[id] / L1 >= t:
                            matchingPairs[id] = 1
                    else:
                        temp[id] = 1
                        
        for id in matchingPairs.keys():
            idDBLP = id
            pairsNo += 1
            if idDBLP in truthD:
                ids = truthD[idDBLP]
                for id in ids:
                    if id == ncid:
                        tp += 1
                        break
            else:
                fp += 1

    return False


def elimina_elementos_dentro_dictB(array_para_descarte, array_para_descarte_igual, elementos_para_descarte):
    indice = 0
    for (tempo_inserido) in array_para_descarte_igual:
        if tempo_inserido < elementos_para_descarte:
            indice += 1
        else:
            del array_para_descarte[:indice]
            del array_para_descarte_igual[:indice]
            break


def exclui_blocos(dictB, dictB_igual, tempoQueFoiInseridoNaEstrutura,tamanhoDosBlocos):
    for l, blocos_da_pos in enumerate(dictB_igual):
        for key, bloco_unico in blocos_da_pos.items():
            if bloco_unico[-1] < tempoQueFoiInseridoNaEstrutura - 300 and tamanhoDosBlocos[(key, l)] > 100:
                tamanhoDosBlocos[(key, l)] -= 100
            break

In [34]:
df1 = pd.read_csv("../00-datasets/ncvoter42.csv", sep=",", encoding="utf-8", keep_default_na=False)
df2 = pd.read_csv("../00-datasets/perturbed_recordsNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truth = pd.read_csv("../00-datasets/ground_truthNC_voter.csv", sep=",", encoding="utf-8", keep_default_na=False)
truthD = dict()
for i, r in truth.iterrows():
    novoId = r["novoId"]
    antigoId = r["antigoId"]
    if antigoId in truthD:
        ids = truthD[antigoId]
        ids.append(novoId)
    else:
        truthD[antigoId] = [novoId]

t = 0.5
TP = 40893
eps = 0.1
w = 1000
delta = 0.1
L = math.ceil(math.log(1 / delta) / (2 * (eps ** 2)))
eps = 0.01
L1 = int(1 / (2 * eps))
print("L=", L, "L1=", L1)
q = 2
dictB = [dict() for l in range(L)]
dictB_igual = [dict() for l in range(L)]
tp = 0
fp = 0
pairsNo = 0
nbS = 1
naS = 1
offsetA = 50
offsetB = 50
blockingTime = 0
matchingTime = 0


tempoQueFoiInseridoNaEstrutura = 0 # esse é o valor que sera colocado junto com o id, seria a posiçaõ do elemento no array
elementos_para_descarte = 50 # esse é a quantidade de elementos que serão descartados
acompanhamentoIndicePorBloco = {} #essa estrutura é um indice que vai ser usada para saber qual a posição do elemento que será descartado
tamanhoDosBlocos = {}
tempo_permanencia = []


L= 116 L1= 50


In [35]:
while True:
    st = time.time()
    for index1 in range(naS, naS + offsetA):
        if index1 >= len(df1):
            break
        rr = df1.iloc[index1, 0:69]
        
        ncid = rr["ncid"]
        first_name = rr["first_name"]
        last_name = rr["last_name"]
        registr_dt = rr["registr_dt"]
        age_at_year_end = rr["age_at_year_end"]
        srec = first_name + " " + last_name + " " + str(registr_dt) + " " + str(age_at_year_end)
        key = ""
        
        for l in range(L):
            key = str(str_to_MinHash(srec.lower(), 2, l))
            d = dictB[l]
            d_igual = dictB_igual[l]
            if key in d:
                ids = d[key]
                ids_igual = d_igual[key]
                tamanho_atual = tamanhoDosBlocos[(key, l)]
                if len(ids) < tamanho_atual:
                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                else:
                    qtd_descarte, elementoAtualParaDescarte = acompanhamentoIndicePorBloco[(key, l)]
                    elimina_elementos_dentro_dictB(ids, ids_igual, elementoAtualParaDescarte)
                    acompanhamentoIndicePorBloco[(key, l)] = [qtd_descarte + 1, elementoAtualParaDescarte + elementos_para_descarte ]

                    array_normalizado = normaliza_para_0(ids_igual, elementoAtualParaDescarte - elementos_para_descarte)
                    media = mean(array_normalizado)
                    tempo_permanencia.append(media)

                    ids.append(ncid)
                    ids_igual.append(tempoQueFoiInseridoNaEstrutura)
                    exclui_blocos(dictB, dictB_igual, tempoQueFoiInseridoNaEstrutura, tamanhoDosBlocos)
                    tamanhoDosBlocos[(key, l)] += 100
                    
            else:
                d[key] = [ncid]
                d_igual[key] = [tempoQueFoiInseridoNaEstrutura]
                acompanhamentoIndicePorBloco[(key, l)] = [0, elementos_para_descarte,]
                tamanhoDosBlocos[(key, l)] = w
            

        tempoQueFoiInseridoNaEstrutura += 1
    
    end = time.time()

    blockingTime += (end - st)
    st = time.time()
    termination = matching()  
    end = time.time()
    matchingTime += (end - st)
    if termination:
            break

    nbS += offsetB
    naS += offsetA

print("blocking time (in mins)", blockingTime / 60)
print("matching time (in mins)", matchingTime / 60)
if tp + fp > 0:
    print("TP=", tp, "Recall=", tp / TP, "Precision=", tp / (tp + fp), "pairsNo=", pairsNo)

blocking time (in mins) 1.3826363921165465
matching time (in mins) 12.156407487392425
TP= 34941 Recall= 0.8544494167705964 Precision= 0.23083326176429783 pairsNo= 267345


In [36]:
mean(tempo_permanencia)

11997.48877154634

In [38]:
from collections import Counter

# Agrupa os valores em intervalos de 100
intervalos = [x // 100 for x in tempo_permanencia]

# Conta a frequência de cada intervalo
contador = Counter(intervalos)

# Exibe o resultado
contador

Counter({147.0: 254,
         146.0: 240,
         139.0: 223,
         140.0: 217,
         141.0: 215,
         151.0: 212,
         145.0: 210,
         136.0: 200,
         119.0: 198,
         148.0: 196,
         142.0: 196,
         120.0: 195,
         153.0: 195,
         131.0: 194,
         143.0: 194,
         158.0: 193,
         116.0: 193,
         121.0: 192,
         122.0: 192,
         117.0: 190,
         133.0: 190,
         152.0: 190,
         134.0: 189,
         144.0: 187,
         150.0: 187,
         102.0: 184,
         114.0: 184,
         132.0: 184,
         138.0: 184,
         129.0: 183,
         112.0: 182,
         118.0: 180,
         162.0: 180,
         123.0: 179,
         149.0: 178,
         115.0: 177,
         124.0: 177,
         105.0: 175,
         154.0: 173,
         135.0: 172,
         90.0: 171,
         113.0: 171,
         159.0: 170,
         125.0: 170,
         171.0: 169,
         155.0: 168,
         164.0: 168,
         100.0

In [43]:
mean(tempo_permanencia)

11997.48877154634

In [40]:
tempo_permanencia

[630.3079331941545,
 620.1443514644351,
 657.1616580310881,
 689.2120640904807,
 713.9874739039666,
 688.7523719165085,
 720.6124763705104,
 773.8498964803313,
 772.9639175257732,
 747.0982758620689,
 756.6868512110726,
 862.7758081334724,
 790.7401129943503,
 786.4664371772806,
 845.9042253521127,
 832.0193089430894,
 917.8343558282209,
 865.3405172413793,
 856.5009380863039,
 952.956644674835,
 854.9243027888447,
 919.7480719794345,
 1085.1352757544225,
 963.8161157024794,
 956.1771771771772,
 998.331780055918,
 945.9028662420383,
 943.9862778730703,
 928.2518409425626,
 1041.2111587982833,
 995.0443388756928,
 876.7634517766497,
 1191.4798122065727,
 1034.8615528531338,
 1024.099853157122,
 1093.1132852729145,
 995.3137388926863,
 1030.2417061611375,
 1076.851401869159,
 1201.3864337101747,
 1129.2045995241872,
 1092.1350427350428,
 1074.1553113553114,
 1289.6408934707904,
 1093.7107776261937,
 1132.7034834324554,
 1057.4916879795396,
 1117.2927366104182,
 1186.6735042735042,
 807.1

In [41]:
import numpy as np

# Seus dados (exemplo com os primeiros valores mostrados)
data = np.array(tempo_permanencia)

# Métricas calculadas
stats = {
    "Total de dados": len(data),
    "Média": np.mean(data),
    "Mediana": np.median(data),
    "Desvio Padrão": np.std(data),
    "Mínimo": np.min(data),
    "Máximo": np.max(data),
    "Amplitude (Max-Min)": np.ptp(data),
    "Quartis": {
        "Q1 (25%)": np.percentile(data, 25),
        "Q2 (50%)": np.percentile(data, 50),
        "Q3 (75%)": np.percentile(data, 75)
    },
    "Assimetria (Skewness)": float(pd.Series(data).skew()),
    "Curtose": float(pd.Series(data).kurt())
}

In [42]:
stats

{'Total de dados': 26233,
 'Média': np.float64(11997.488771546337),
 'Mediana': np.float64(12174.422767314702),
 'Desvio Padrão': np.float64(5340.830060890574),
 'Mínimo': np.float64(620.1443514644351),
 'Máximo': np.float64(38481.751764705885),
 'Amplitude (Max-Min)': np.float64(37861.60741324145),
 'Quartis': {'Q1 (25%)': np.float64(8045.954805491991),
  'Q2 (50%)': np.float64(12174.422767314702),
  'Q3 (75%)': np.float64(15660.165153147607)},
 'Assimetria (Skewness)': 0.4390664765621671,
 'Curtose': 1.3311266684376224}